In [73]:
import datashader as ds
import pandas as pd
from colorcet import fire
from datashader import transfer_functions as tf
from datashader.bokeh_ext import InteractiveImage
import geopandas
import requests
from bokeh.models import BoxZoomTool
from bokeh.plotting import figure, output_notebook, show
from bokeh.tile_providers import STAMEN_TERRAIN

output_notebook()

Loading BokehJS ...

In [25]:
url = 'http://lifewatch.cartodb.com/api/v2/sql?format=geojson&q=SELECT * FROM bird_tracking'

In [26]:
response = requests.get(url)

In [28]:
with open('bird_tracking.geojson', 'wb') as f:
    f.write(response.content)

In [30]:
del response

In [74]:
df = geopandas.read_file('bird_tracking.geojson')

In [31]:
df.head()

cartodb_id  altitude  device_info_serial  speed_2d  longitude   latitude  \
0       55012        -2                 719       NaN   5.578757  53.031496   
1      311215        86                 833       NaN   2.283519  49.940810   
2      459132        10                 851       NaN   3.209604  51.300984   
3        8108        62                 719       NaN   3.207726  51.285391   
4       13736        86                 719       NaN   3.219947  51.208479   

             date_time  _feature_count                    geometry  
0  2014-06-05T05:13:31               1  POINT (5.578757 53.031496)  
1  2013-08-03T00:56:10               1   POINT (2.283519 49.94081)  
2  2013-05-30T19:22:03               1  POINT (3.209604 51.300984)  
3  2013-06-27T11:14:29               1  POINT (3.207726 51.285391)  
4  2013-07-13T11:17:39               1  POINT (3.219947 51.208479)

In [32]:
len(df)

666519

In [45]:
x_range, y_range = ((min(df['longitude']), max(df['longitude'])), (min(df['latitude']), max(df['latitude'])))
x_range, y_range

((-17.6261451, 7.4792583), (12.354424, 54.3338823))

In [46]:
plot_width  = int(750)
plot_height = int(plot_width//1.2)

In [47]:
def create_image(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(df, 'longitude', 'latitude')
    img = tf.shade(agg, cmap=fire)
    return tf.dynspread(img, threshold=0.3, max_px=4)
    
def base_plot(tools='pan,wheel_zoom,reset',plot_width=plot_width, plot_height=plot_height, **plot_args):
    p = figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
        x_range=x_range, y_range=y_range, outline_line_color=None,
        min_border=0, min_border_left=0, min_border_right=0,
        min_border_top=0, min_border_bottom=0, **plot_args)
    
    p.axis.visible = False
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    
    p.add_tools(BoxZoomTool(match_aspect=True))
    
    return p

In [69]:
p = base_plot()
#p.add_tile(STAMEN_TERRAIN)
InteractiveImage(p, create_image)

In [75]:
import holoviews as hv
import geoviews as gv
from holoviews.operation.datashader import datashade

In [78]:
%%opts Graph [width=1000 height=600]

map_tiles = gv.tile_sources.CartoDark
points     = hv.Points(df, ['longitude', 'latitude'])
#taxi_trips = datashade(points, x_sampling=1, y_sampling=1, cmap=fire, width=1000, height=600)
taxi_trips = datashade(points, cmap=fire, width=1000, height=600)

map_tiles * taxi_trips

:DynamicMap   []
   :Overlay
      .WMTS.I :WMTS   [Longitude,Latitude]
      .RGB.I  :RGB   [longitude,latitude]   (R,G,B,A)